# PB016: Artificial Intelligence I, lab 3 - Heuristic search

Today we'll deal with heuristic algorithms for state space search. We'll focus namely on:
1. __Best-first search__
2. __A* search__
3. __A* search applied to a game (8-puzzle)__

---

## 1. [Best-First Search](https://en.wikipedia.org/wiki/Best-first_search)

__Basic facts__
- A search algorithm that preferentially visits the most "promising" vertices while searching for the goal vertex.
- The promise of a vertex is usually defined by a heuristic rule (i.e. heuristic) that depends on the nature of the problem.
- Slightly more formally - a heuristic for estimating the promise of a vertex $n$ is a function $h(n)$, which generally depends on one or more of the following:
 - the properties of the vertex $n$,
 - the properties of the goal vertex,
 - information gained during the search so far,
 - any other information related to the problem that is being solved.
- Many instances exist, e.g. [Dijkstra's algorithm](https://en.wikipedia.org/wiki/Dijkstra%27s_algorithm), [B\* search](https://en.wikipedia.org/wiki/B*) or [A\* search](https://en.wikipedia.org/wiki/A*_search_algorithm) (covered below).

### Problem definition for purely heuristic search


- Finding a path between Arad to Bucharest on a simplified map of Romania (for the sake of simplicity, we won't bother about cycles, etc., here or in any of the following exercises).
- At first we represent the map as a graph.

In [ ]:
# creating a simplified map of Romania

import networkx as nx

# creating a graph representing the map
romania_map = nx.Graph()

# filling the graph with edges representing direct connections (i.e. roads)
# between the towns and their length

romania_map.add_edge('Arad', 'Zerind', cost=75)
romania_map.add_edge('Arad', 'Sibiu', cost=140)
romania_map.add_edge('Arad', 'Timisoara', cost=118)
romania_map.add_edge('Bucharest', 'Urziceni', cost=85)
romania_map.add_edge('Bucharest', 'Pitesti', cost=101)
romania_map.add_edge('Bucharest', 'Giurgiu', cost=90)
romania_map.add_edge('Bucharest', 'Fagaras', cost=211)
romania_map.add_edge('Craiova', 'Drobeta', cost=120)
romania_map.add_edge('Craiova', 'Rimnicu', cost=146)
romania_map.add_edge('Craiova', 'Pitesti', cost=138)
romania_map.add_edge('Drobeta', 'Mehadia', cost=75)
romania_map.add_edge('Eforie', 'Hirsova', cost=86)
romania_map.add_edge('Fagaras', 'Sibiu', cost=99)
romania_map.add_edge('Hirsova', 'Urziceni', cost=98)
romania_map.add_edge('Iasi', 'Vaslui', cost=92)
romania_map.add_edge('Iasi', 'Neamt', cost=87)
romania_map.add_edge('Lugoj', 'Timisoara', cost=111)
romania_map.add_edge('Lugoj', 'Mehadia', cost=70)
romania_map.add_edge('Oradea', 'Zerind', cost=71)
romania_map.add_edge('Oradea', 'Sibiu', cost=151)
romania_map.add_edge('Pitesti', 'Rimnicu', cost=97)
romania_map.add_edge('Rimnicu', 'Sibiu', cost=80)
romania_map.add_edge('Urziceni', 'Vaslui', cost=142)

# coordinates of the towns on the map (for computing the air distance between
# any two towns)

romania_coordinates = {
    'Arad':(91, 492), 'Bucharest':(400, 327), 'Craiova':(253, 288),
    'Drobeta':(165, 299), 'Eforie':(562, 293), 'Fagaras':(305, 449),
    'Giurgiu':(375, 270), 'Hirsova':(534, 350), 'Iasi':(473, 506),
    'Lugoj':(165, 379), 'Mehadia':(168, 339), 'Neamt':(406, 537),
    'Oradea':(131, 571), 'Pitesti':(320, 368), 'Rimnicu':(233, 410),
    'Sibiu':(207, 457), 'Timisoara':(94, 410), 'Urziceni':(456, 350),
    'Vaslui':(509, 444), 'Zerind':(108, 531)
}

#### Visualising the map of Romania

![Romania](https://www.fi.muni.cz/~novacek/courses/pb016/labs/img/romania.png)

#### Data structure required for the search
- Best-first search typically uses a [priority queue](https://en.wikipedia.org/wiki/Priority_queue) for picking the most promising vertices.
- We'll be using an implementation from the standard library in Python.

In [ ]:
from queue import PriorityQueue

pq = PriorityQueue() # initialising the priority queue

# test of the priority queue

# see that we always insert pairs (priority, node)
pq.put((9999., 'Arad'))
pq.put((0., 'Bucharest'))
pq.put((8888., 'Zerind'))
pq.put((7777., 'Sibiu'))

# minimal value is taken out first
while not pq.empty():
    # check how we take out items from the priority queue
    value, node = pq.get()
    print(f'An element with the lowest weight ({value}): {node}')

### __Exercise 1.1: Best-first search - heuristic__
- For the actual implementation of finding the path between two towns by the best-first search algorithm, one of the applicable heuristics is the air distance between the towns being visited and the goal (Bucharest).
 - Note: The air distance between two points A and B is typically computed from the coordinates of A and B using the  [Euclidean distance](https://en.wikipedia.org/wiki/Euclidean_distance).
- Implement this heuristic.

In [ ]:
import math  # guess which math fn do we need?

def heuristic(current, goal='Bucharest'):
    """Compute the value of distance-based heuristic for finding the path
    between the input towns.

    Parameters
    ----------
    current : str
        The name of the town from which the path to the goal is currently to
        be found.
    goal : str, optional (default is 'Bucharest') for this specific assignment
        The name of the goal town.

    Returns
    -------
    float
        The value of the `current` town heuristic, i.e., how promising it is to
        reach the goal from it.
    """

    h_val = float('inf') # returns infinity if there's a wrong input, etc.
    # TODO - COMPLETE YOURSELVES
    return h_val


# checking the correctness of the heuristic
if round(heuristic('Arad', 'Bucharest'), 6) == 350.294162:
    print('OK.')
else:
    print('Not quite OK.')

### __Exercise 1.2: Greedy best-first search - a basic version__
- The search is greedy - the vertex to be explored first is always the one with the best heuristic value.
- In the basic version we're only testing the path existence.

In [ ]:
def greedy_best_first_search_test_only(graph, h, start='Arad', goal='Bucharest'):
    """Uses the greedy best-first search algorithm to test for existence of the
    path between the two input nodes.

    Parameters
    ----------
    graph : networkx.Graph
        The graph representing the map to be searched.
    h : typing.Callable (i.e., a function)
        The heuristic function to be used for computing how promising the
        particular searched towns for reaching the goal town.
    start : str, optional (default is 'Arad') for this specific assignment
        The name of the starting town.
    goal : str, optional (default is 'Bucharest') for this specific assignment
        The name of the goal town.

    Returns
    -------
    bool
        Whether or not a path has been found between the `start` and `goal`
        towns.
    """

    found = False # default result

    # TODO - COMPLETE YOURSELVES

    return found

In [ ]:
# testing the result of the search
if greedy_best_first_search_test_only(romania_map, heuristic):
    print('There is a path between Arad and Bucharest.')
else:
    print('There is no path between Arad and Bucharest.')

### __Exercise 1.3: Best-first search - a version with printing out the path__
- Augment the search by
 - keeping track of the predecessors of vertices on the searched path;
 - printing out the path with its final cost (i.e. the total traveled distance between Arad and Bucharest as a sum of the lengths of the particular direct connections between the towns on the path).

In [ ]:
def greedy_best_first_search(graph, h, start='Arad', goal='Bucharest'):
    """Uses the greedy best-first search algorithm to test for existence of
    the path between the two input nodes.

    Parameters
    ----------
    graph : networkx.Graph
        The graph representing the map to be searched.
    h : typing.Callable (i.e., a function)
        The heuristic function to be used for computing how promising the
        particular searched towns for reaching the goal town.
    start : str, optional (default is 'Arad') for this specific assignment
        The name of the starting town.
    goal : str, optional (default is 'Bucharest') for this specific assignment
        The name of the goal town.

    Returns
    -------
    tuple
        A pair consisting of the following elements:
        - A `bool` variable that records whether or not a path has been found
          between the `start` and `goal` towns.
        - A `dict` variable that records the path itself as a mapping of the
          towns in the path to their predecessors.
    """

    found = False
    frontier = PriorityQueue()
    frontier.put((h(start, goal), start))
    came_from = {} # the map of precedessors
    came_from[start] = None # initialising the map

    # TODO - COMPLETE YOURSELVES

    return found, came_from


def reconstruct_path(graph, came_from, start='Arad', goal='Bucharest'):
    """Reconstructs the path from start to goal town (will be also used for A*).

    HINT - to get an edge's cost, you can use the `graph[from][to]['cost']`
           notation!

    Parameters
    ----------
    graph : networkx.Graph
        The graph representing the map to be searched.
    came_from : dict
        A dictionary mapping the towns in the path to their predecessors.
    start : str, optional (default is 'Arad') for this specific assignment
        The name of the starting town.
    goal : str, optional (default is 'Bucharest') for this specific assignment
        The name of the goal town.

    Returns
    -------
    tuple
        A pair consisting of the following elements:
        - An `int` `list` variable that records the cost (i.e., length) of the
          path between the `start` and `goal` towns.
        - A `list` that records the path itself.
    """

    current = goal # we're going backwards, i.e. from the goal
    path = [] # empty path
    cost = 0 # zero cost of an empty path

    # TODO - COMPLETE YOURSELVES

    return cost, path

In [ ]:
# testing the result of the search and printing out the path
start, end = 'Arad', 'Bucharest'
found, came_from = greedy_best_first_search(romania_map, heuristic, start=start,
                                            goal=end)
if found:
    print('There is a path between Arad and Bucharest.')
    cost, path = reconstruct_path(romania_map, came_from, start=start, goal=end)
    print('  - the cost is:', cost)
    print('  - the path is:', path)
else:
    print('There is no path between Arad and Bucharest.')

---

## 2. [A\* Search](https://en.wikipedia.org/wiki/A*_search_algorithm)

__Basic facts__
- One of the most famous forms of best-first search.
- It combines a heuristic estimate of the most promising vertices with the actual cost of the path so far.
- Guaranteed to find an optimal solution with the proper choice of a heuristic.

### __Exercise 2.1: Extending the best-first search to A*__
- In addition to the vertex promise (defined by the heuristic) we also take into account the actual cost of the path so far.
- Slightly more formally, in each step of the search, we're prioritising the vertices $n$ that minimise the value $f(n) = g(n)+h(n)$, where:
 - $g(n)$ is the actual cost of the path so far (for the problem of finding a path between cities, it is thus the sum of the lengths of the direct connections between the currently traversed towns);
 - $h(n)$ is the heuristic estimate of the cost of making it from the current vertex to the goal one (just like in the greedy best-first search).
- Implement this version of best-first search and compare it with the previous one.

In [ ]:
def astar_search(graph, h, start='Arad', goal='Bucharest'):
    """Uses the A* search to pre-compute a path between two nodes.

    Parameters
    ----------
    graph : networkx.Graph
        The graph representing the map to be searched.
    h : typing.Callable (i.e., a function)
        The heuristic function to be used for computing how promising the
        particular searched towns for reaching the goal town.
    start : str, optional (default is 'Arad') for this specific assignment
        The name of the starting town.
    goal : str, optional (default is 'Bucharest') for this specific assignment
        The name of the goal town.

    Returns
    -------
    tuple
        A pair consisting of the following elements:
        - A `bool` variable that records whether or not a path has been found
          between the `start` and `goal` towns.
        - A `dict` variable that records the path itself as a mapping of the
          towns in the path to their predecessors.
    """

    frontier = PriorityQueue()
    frontier.put((h(start, goal), start))
    found = False
    came_from = {}
    came_from[start] = None
    cost_so_far = {} # adding the map of actual cost of visiting the vertices
    cost_so_far[start] = 0 # zero cost for the starting vertex

    # TODO - COMPLETE YOURSELVES

    return found, came_from

In [ ]:
# testing the result of the search and printing out the path
start, end = 'Arad', 'Bucharest'
found, came_from = astar_search(romania_map, heuristic, start, end)
if found:
    print(f'There is a path between {start} and {end}.')
    cost, path = reconstruct_path(romania_map, came_from, start, end)
    print('  - the cost is:', cost)
    print('  - the path is:', path)
else:
    print(f'There is no path between {start} and {end}.')

---

## 3. A* search applied to a game (8-puzzle)

__Basic facts__
- A puzzle consisting of a game board with 9 fields (3x3).
- On 8 of these fields, 8 square playing blocks are placed (marked by numbers between 1 and 8). The remaining field is empty.
- The goal is to move the blocks around so that they are ordered from 1 to 8.
- One can only move the blocks around vertically or horizontally to the empty field.
 - In our representation of the problem, this will correspond to "moving" the empty field LEFT, RIGHT, UP or DOWN.

__An example__ - "unfolding" of possible paths towards the goal from a particular state of the 8-puzzle:

![8puzzle](https://www.fi.muni.cz/~novacek/courses/pb016/labs/img/8puzzle.jpg)

### Representation of the 8-puzzle problem and helper functions
- One can represent the board positions using a tuple of $9$ integers from $0$ to $8$, where $0$ corresponds to the empty field.
- For instance, `(8,1,3,0,2,4,7,6,5)` corresponds to a board where the first row from the top contains the blocks $8,1,3$, the second starts with the empty field followed by $2,4$ and the third row contains the blocks $7,6,5$. This is the first board from the left in the bottom row in the example above.
- The particular states of the problem solution space can be represented as pairs with the following elements:
 - the current positions of the blocks on the board,
 - the sequence of moves (i.e. "transitions" of the empty field) from the starting board to the current state.
- The expansion of the current state is performed via a function that generates all possible next states except the one that immediately preceded the current state (to make sure we don't just shuffle the blocks there and back).

In [ ]:
# mapping the natural language representation of moving the empty field to the
# corresponding index changes on a matrix representation of the playing board
move_map = {
    'UP' : (-1,0),
    'DOWN' : (1,0),
    'LEFT' : (0,-1),
    'RIGHT' : (0,1)
}

# mapping of the inverse moves (to detect trivially repeating consecutive states)
move_inverse = {
    'LEFT': 'RIGHT',
    'RIGHT': 'LEFT',
    'UP': 'DOWN',
    'DOWN': 'UP'
}


def transform_board(board, move):
    """Moves the empty field 'LEFT', 'RIGHT', 'UP' or 'DOWN' and swaps it with
    the corresponding tile.

    Parameters
    ----------
    board : tuple
        A tuple representation of the board - the elements with indices 0,1,2
        representing the top row (from left to right), the elements with indices
        3,4,5 representing the middle row (from left to right) and the elements
        with indices 6, 7, 8 representing the bottom row (from left to right).
        The values of the tuple elements represent the pieces of the game, with
        0 corresponding to the empty field.
    move : str (one of 'LEFT', 'RIGHT', 'UP' or 'DOWN' accepted)
        The move to be executed.

    Returns
    -------
    tuple
        A tuple representation of the board after executing the (valid) move.
    """

    board_matrix = {} # simple matrix representation of the board
    zero_i, zero_j = -1, -1 # empty field position (nonsense by default)

    # filling the matrix from the input "flat" representation of the board
    for k in range(9):
        i, j = k // 3, k % 3
        board_matrix[(i, j)] = board[k]
        if board[k] == 0:
            zero_i, zero_j = i, j

    if zero_i == -1 or zero_j == -1: # checking for nonsense empty field
        return board # empty field is not valid, return the board unchanged

    # generating a new index of the empty field
    delta_i, delta_j = move_map[move]
    new_zero_i, new_zero_j = zero_i + delta_i, zero_j + delta_j

    # generating a new matrix representation of the board for a valid input move
    if new_zero_i >= 0 and new_zero_i <= 2 and new_zero_j >= 0 and new_zero_j <= 2:
        swap_block = board_matrix[(new_zero_i, new_zero_j)]
        board_matrix[(new_zero_i, new_zero_j)] = 0
        board_matrix[(zero_i, zero_j)] = swap_block

    # "flattening" the new matrix and returning the results
    new_board = []
    for i in range(3):
        for j in range(3):
            new_board.append(board_matrix[(i,j)])

    return tuple(new_board)


# NOTE - use this for generating neighbors if following the sample code
def expand_state(state):
    """Generates all possible non-repeating states from the current one.

    Parameters
    ----------
    state : tuple
        A pair with the following elements:
        - a tuple representation of the board (c.f. the `transform_board`
          function documentation for details)
        - a list containing the sequence of moves that have led to the current
          board from an initial state (from the first to the last move)

    Returns
    -------
    list
        A list of length up to 4, containing all possible new states (pairs of
        board representations and corresponding lists of moves that have led to
        them) that can be generated from the input board, moving the empty
        field 'LEFT', 'RIGHT', 'UP' or 'DOWN'.
    """

    # unpacking of the states and the sequence of the past moves
    current_board, moves = state

    # generating the previous board by a reversing the last move (if it exists)
    previous_board = ()
    if len(moves) > 0:
        previous_board = transform_board(current_board, move_inverse[moves[-1]])

    # generating all possible next states
    expanded_states = []
    for move in move_map.keys():
        # generating the board
        new_board = transform_board(current_board,move)
        # validating the board
        if new_board != previous_board and new_board != current_board:
            new_moves = moves + [move] # update move history
            expanded_states.append((new_board, new_moves))

    return expanded_states


def print_board(board):
    """Helper function for printing out the board.

    Parameters
    ----------
    board : tuple
        A tuple representation of the board (c.f. the `transform_board`
        function documentation for details).
    """

    block_map = {0:' ', 1:'1', 2:'2', 3:'3', 4:'4', 5:'5', 6:'6', 7:'7', 8:'8'}
    print('| '+' | '.join([block_map[x] for x in board[:3]])+' |')
    print('| '+' | '.join([block_map[x] for x in board[3:6]])+' |')
    print('| '+' | '.join([block_map[x] for x in board[6:]])+' |')

In [ ]:
# testing the way the states are generated
print('Current board (after moving the empty field DOWN before):')
print_board((8,1,3,0,2,4,7,6,5))
print('Previous board:')
print_board(transform_board((8,1,3,0,2,4,7,6,5),move_inverse['DOWN']))
print('\n---------------\n')
for state in expand_state(((8,1,3,0,2,4,7,6,5),['DOWN'])):
    board, moves = state
    print('Next possible board:')
    print_board(board)
    print('Sequence of corresponding moves from the current state:',moves,'\n')

### __Exercise 3.1: Defining heuristics for solving the 8-puzzle using A\* search__
- The cost of the current state is the number of moves from the initial board.
- Define possible heuristics for estimating the promise of the next possible moves.
- Possible options are for instance:
 1. [Hamming distance](https://en.wikipedia.org/wiki/Hamming_distance) - the number of blocks that are not in the goal position,
 2. [Manhattan distance](https://en.wikipedia.org/wiki/Taxicab_geometry) - sum of the vertical and horizontal distances of all blocks from their goal positions.
- Any other ideas?

In [ ]:
def hamming_distance(board, goal_board=(1,2,3,4,5,6,7,8,0)):
    """Computes Hamming distance between given `board` and `goal_board`.

    Parameters
    ----------
    board : tuple
        A tuple representation of the board for which the heuristric is to be
        computed (c.f. the `transform_board` function documentation for
        details).
    goal_board : tuple (optional, the default being the desired ordered
    configuration of the tiles)
        A tuple representation of the goal board.

    Returns
    -------
    int
        The value of the Hamming distance between the input board and the
        desired goal configuration.
    """

    # infinity for invalid board formats
    if len(board) != len(goal_board):
        return float('inf')

    distance = 0 # deault zero distance

    # TODO - COMPLETE YOURSELVES (note: the flat representation of the board
    #        comes in handy here)

    return distance


def manhattan_distance(board, goal_board=(1,2,3,4,5,6,7,8,0)):
    """Computes Manhattan distance between given `board` and `goal_board`.

    Parameters
    ----------
    board : tuple
        A tuple representation of the board for which the heuristric is to be
        computed (c.f. the `transform_board` function documentation for
        details).
    goal_board : tuple (optional, the default being the desired ordered
    configuration of the tiles)
        A tuple representation of the goal board.

    Returns
    -------
    int
        The value of the Manhattan distance between the input board and the
        desired goal configuration.
    """

    # infinity for invalid board formats
    if len(board) != len(goal_board):
        return float('inf')

    distance = 0 # default zero distance

    # TODO - COMPLETE YOURSELVES (note: here it's more convenient to work with
    #        the matrix representation of the board)

    return distance

In [ ]:
# testing the distances
board1 = (8,1,3,0,2,4,7,6,5)
board2 = (1,2,3,4,5,6,7,8,0)
print('Board 1:')
print_board(board1)
print('Board 2:')
print_board(board2)
print('-'*80)
print('Hamming distance from the goal:')
print('  - board 1:', hamming_distance(board1))
print('  - board 2:', hamming_distance(board2))
print('Manhattan distance from the goal:')
print('  - board 1:', manhattan_distance(board1))
print('  - board 2:', manhattan_distance(board2))

### __Exercise 3.2: The actual 8-puzzle solution via A\* search and the defined heuristics__
- Adapt the A\* code for finding a path between towns from the previous exercises to this problem.
- Use the heuristics defined above.

In [ ]:
def astar_search_8puzzle(starting_board, goal_board=(1,2,3,4,5,6,7,8,0),
                         h=hamming_distance):
    """Uses the A* search to solve the 8 puzzle (find path to the goal).

    Parameters
    ----------
    starting_board : tuple
        A tuple representation of the initial board (c.f. the `transform_board`
        function documentation for details).
    goal_board : tuple (optional, the default being the desired ordered
        configuration of the tiles)
    h : typing.Callable (i.e., a function)
        The heuristic to measure the promise of the boards for reaching the
        final configuration.


    Returns
    -------
    tuple
        A pair consisting of the following elements:
        - The solution state (i.e., the final board tuple representation and the
          sequence of moves that have led to it from the initial board
          configuration).
        - The number of states explored while finding the solution (i.e., the
          total number of nodes expanded in the implicit graph representing the
          search space).
    """

    frontier = PriorityQueue() # creating the queue
    starting_state = (starting_board, []) # initial board, no previous moves
    cost_so_far = {} # cost of explored board (number of moves from the start)
    cost_so_far[starting_board] = 0

    frontier.put((h(starting_board, goal_board), starting_state))
    solution = None # final state (if it was reached)
    states_explored = 1 # number of searched states

    # processing the queue until the goal is found or all states are explored

    # TODO - COMPLETE YOURSELVES

    return solution, states_explored


def print_solution(start, moves):
    """Prints the path towards the solution.

    Parameters
    ----------
    start : tuple
        A tuple representation of the initial board from which the game starts
        (c.f. the `transform_board` function documentation for details).
    moves : list
        A list of moves that have led from the initial board to the final
        solution.
    """

    current_board = start
    for move in moves:
        print_board(current_board)
        print()
        current_board = transform_board(current_board,move)
    print_board(current_board)

In [ ]:
# testing the search
start1 = (0, 1, 3, 4, 2, 5, 7, 8, 6) # has solution
start2 = (2, 4, 3, 1, 5, 6, 7, 8, 0) # has solution
start3 = (1, 2, 3, 4, 5, 7, 8, 6, 0) # has solution
start4 = (1, 2, 3, 4, 5, 6, 8, 7, 0) # no solution
for starting_board in [start1, start2, start3, start4]:
    print('Starting board:')
    print_board(starting_board)
    print('... searching with Hamming heuristic ...')
    solution_h, states_h = astar_search_8puzzle(starting_board,
                                                h=hamming_distance)
    print(f'  - searched {states_h} states')
    print('... searching with Manhattan heuristic ...')
    solution_m, states_m = astar_search_8puzzle(starting_board,
                                                h=manhattan_distance)
    print(f'  - searched {states_m} states')
    if solution_h: # testing for one solution only is OK if they exist at all
        print('Solution exists and looks like:')
        print_solution(starting_board, solution_h[1])
    else:
        print('No solution found.')
    print('-'*80)

---

#### _Final note_ - some materials used in this notebook are adapted works licensed by their original authors as follows:
- Romania map:
 - Adapted from [GitHub AIMA code](https://github.com/aimacode/aima-python/blob/master/search.ipynb)
 - Author: The [AIMA-Python](https://github.com/aimacode/aima-python/graphs/contributors) collective
 - License: [MIT](https://opensource.org/licenses/MIT)
- 8puzzle figure:
 - Adapted from [webu GeeksForGeeks](https://www.geeksforgeeks.org/8-puzzle-problem-using-branch-and-bound/)
 - Author: [unknown / GeeksForGeeks collective](contribute@geeksforgeeks.org)
 - Original source: [GeeksForGeeks](https://media.geeksforgeeks.org/wp-content/uploads/puzzle-1.jpg)
 - License: N/A